## Retriever And Chain With Langchain 

In [1]:
import os
from dotenv import load_dotenv
load_dotenv()

os.environ["OPENAI_API_BASE"] = os.getenv("OPENAI_API_BASE")
os.environ['OPENAI_API_KEY']=os.getenv('OPENAI_API_KEY')

True

## Loading docs

In [2]:
from langchain_community.document_loaders import PyPDFLoader
loader = PyPDFLoader('imagepro.pdf')
docs=loader.load()
docs

[Document(metadata={'producer': 'Acrobat Distiller 10.1.16 (Macintosh)', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2017-08-08T11:22:14+01:00', 'author': 'Rafael C. Gonzalez', 'moddate': '2018-11-10T17:53:17+03:30', 'title': 'Digital Image Processing, 4e', 'trapped': '/False', 'source': 'imagepro.pdf', 'total_pages': 1022, 'page': 0, 'page_label': 'Cover'}, page_content='GLOBAL\n \nEDITION\nThis is a special edition of an established \ntitle widely used by colleges and universities \nthroughout the world. Pearson published this \nexclusive edition for the benefit of students \noutside the United States and Canada. If \nyou purchased this book within the United \nStates or Canada, you should be aware that \nit has been imported without the approval of \nthe Publisher or Author. The Global Edition \nis not supported in the United States and \nCanada.\nPearson Global Edition\nGLOBAL\n \nEDITION\nFor these Global Editions, the editorial team at Pearson has \ncollaborated w

## Splitting docs

In [3]:
from langchain_text_splitters import RecursiveCharacterTextSplitter
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=20)
text_splitter.split_documents(docs)[:5]

[Document(metadata={'producer': 'Acrobat Distiller 10.1.16 (Macintosh)', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2017-08-08T11:22:14+01:00', 'author': 'Rafael C. Gonzalez', 'moddate': '2018-11-10T17:53:17+03:30', 'title': 'Digital Image Processing, 4e', 'trapped': '/False', 'source': 'imagepro.pdf', 'total_pages': 1022, 'page': 0, 'page_label': 'Cover'}, page_content='GLOBAL\n \nEDITION\nThis is a special edition of an established \ntitle widely used by colleges and universities \nthroughout the world. Pearson published this \nexclusive edition for the benefit of students \noutside the United States and Canada. If \nyou purchased this book within the United \nStates or Canada, you should be aware that \nit has been imported without the approval of \nthe Publisher or Author. The Global Edition \nis not supported in the United States and \nCanada.\nPearson Global Edition\nGLOBAL\n \nEDITION\nFor these Global Editions, the editorial team at Pearson has \ncollaborated w

In [4]:
documents=text_splitter.split_documents(docs)
documents

[Document(metadata={'producer': 'Acrobat Distiller 10.1.16 (Macintosh)', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2017-08-08T11:22:14+01:00', 'author': 'Rafael C. Gonzalez', 'moddate': '2018-11-10T17:53:17+03:30', 'title': 'Digital Image Processing, 4e', 'trapped': '/False', 'source': 'imagepro.pdf', 'total_pages': 1022, 'page': 0, 'page_label': 'Cover'}, page_content='GLOBAL\n \nEDITION\nThis is a special edition of an established \ntitle widely used by colleges and universities \nthroughout the world. Pearson published this \nexclusive edition for the benefit of students \noutside the United States and Canada. If \nyou purchased this book within the United \nStates or Canada, you should be aware that \nit has been imported without the approval of \nthe Publisher or Author. The Global Edition \nis not supported in the United States and \nCanada.\nPearson Global Edition\nGLOBAL\n \nEDITION\nFor these Global Editions, the editorial team at Pearson has \ncollaborated w

## Vector Store


In [5]:
from langchain_community.embeddings import OpenAIEmbeddings
from langchain_community.embeddings import OllamaEmbeddings
from langchain_community.vectorstores import FAISS

from langchain_huggingface.embeddings import HuggingFaceEmbeddings

# 临时增加代理
os.environ['HTTP_PROXY'] = "http://127.0.0.1:7890"
os.environ['HTTPS_PROXY'] = "http://127.0.0.1:7890"

model_name = "BAAI/bge-large-zh-v1.5"
model_kwargs = {'device': 'cpu', "trust_remote_code":True}
encode_kwargs = {'normalize_embeddings': True}
hf_emb_model = HuggingFaceEmbeddings(
    model_name=model_name,
    model_kwargs=model_kwargs,
    encode_kwargs=encode_kwargs
)

# 去除增加代理
os.environ.pop('HTTP_PROXY')
os.environ.pop('HTTPS_PROXY')

db=FAISS.from_documents(documents[:30], hf_emb_model)

'http://127.0.0.1:7890'

'http://127.0.0.1:7890'

In [6]:
db

In [7]:
query="Department of Agriculture and Farmers Welfare"
result=db.similarity_search(query)
result[0]

Document(id='0a6a5443-657c-4bde-837e-283c2a364fee', metadata={'producer': 'Acrobat Distiller 10.1.16 (Macintosh)', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2017-08-08T11:22:14+01:00', 'author': 'Rafael C. Gonzalez', 'moddate': '2018-11-10T17:53:17+03:30', 'title': 'Digital Image Processing, 4e', 'trapped': '/False', 'source': 'imagepro.pdf', 'total_pages': 1022, 'page': 9, 'page_label': '8'}, page_content='8\n    \nContents\nSome Basic Morphological Algorithms  652\nMorphological Reconstruction  667\nSummary of Morphological Operations on Binary Images  673\nGrayscale Morphology  674\n10\n Image Segmentation  699\nFundamentals  \n700\nPoint, Line, and Edge Detection  \n701\nThresholding  \n742\nSegmentation by Region Growing and by Region Splitting and \nMerging  \n764\nRegion Segmentation Using Clustering and  \nSuperpixels  \n770\nRegion Segmentation Using Graph Cuts\n  \n777\nSegmentation Using Morphological Watersheds\n  \n786\nThe Use of Motion in Segmentation  

## LLM model using 

In [8]:
from langchain_ollama.llms import OllamaLLM
## Load Ollama LLama-3 LLM Model
llm=OllamaLLM(model="deepseek-r1:1.5b")
llm

OllamaLLM(model='deepseek-r1:1.5b')

## Design ChatPrompt Template

In [9]:
from langchain_core.prompts import ChatPromptTemplate
prompt = ChatPromptTemplate.from_template("""
Answer the following question based only on the provided context.
Think step bt step before providing a detailed answer.
I will tip you $1000 if the user finds the answer helpful.
<context>
{context}
</context>                                          
Question: {input}""")

## Chain Introduction || Create Stuff Document Chain

In [10]:
from langchain_classic.chains.combine_documents import create_stuff_documents_chain
document_chain=create_stuff_documents_chain(llm,prompt)

## Retrievers
- A retriever is an interface that returns documents given an unstructured query. It is more general than a vector store. A retriever does not need to be able to store documents, only to return (or retrieve) them. Vector stores can be used as the backbone of a retriever, but there are other types of retrievers as well.
[Learn more](https://python.langchain.com/v0.1/docs/modules/data_connection/retrievers/)

In [11]:
retriever= db.as_retriever()
retriever

VectorStoreRetriever(tags=['FAISS', 'HuggingFaceEmbeddings'], vectorstore=<langchain_community.vectorstores.faiss.FAISS object at 0x76ffc1f39fd0>, search_kwargs={})

## Retrievers Chains
- Retrievers chain: This chain takes in user inquiry, which is then passed to the retriver to fetch relevant documents. Those documents(and original inputs) are then passed to an LLM to generate a response

In [12]:
from langchain_classic.chains import create_retrieval_chain
retrieval_chain=create_retrieval_chain(retriever,document_chain)

## Invoking Any Query now

In [13]:
response=retriever.invoke(input="""image processing with an introduction to techniques for image pattern classification""")
response

[Document(id='8ddc145c-d3b3-4bae-8d2c-d3b0b26d2cff', metadata={'producer': 'Acrobat Distiller 10.1.16 (Macintosh)', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2017-08-08T11:22:14+01:00', 'author': 'Rafael C. Gonzalez', 'moddate': '2018-11-10T17:53:17+03:30', 'title': 'Digital Image Processing, 4e', 'trapped': '/False', 'source': 'imagepro.pdf', 'total_pages': 1022, 'page': 6, 'page_label': '5'}, page_content='Contents\nPreface  9\nAcknowledgments  12\nThe Book Website  13\nThe DIP4E Support Packages  13\nAbout the Authors  14\n1\n Introduction  17\nWhat is Digital Image Processing?  18\nThe Origins of Digital Image Processing  19\nExamples of Fields that Use Digital Image Processing  23\nFundamental Steps in Digital Image Processing  41\nComponents of an Image Processing System  44\n2\n Digital Image Fundamentals  47\nElements of Visual Perception  48\nLight and the Electromagnetic Spectrum  54\nImage Sensing and Acquisition  57\nImage Sampling and Quantization  63\nSo

In [14]:
response=retrieval_chain.invoke({"input":"""image processing with an introduction to techniques for image pattern classification"""})
# document_chain.invoke({"input":"""image processing with an introduction to techniques for image pattern classification"""})

In [15]:
print(response['answer'])

Based on the provided context from the textbook, digital image processing introduces several foundational concepts necessary for understanding how images are processed and analyzed. The question about image pattern classification can be addressed by examining these fundamentals.

The textbook covers elements of visual perception, light properties (electromagnetic spectrum), and basic mathematical tools relevant to image processing. These topics provide a structural basis that is essential for grasping more advanced techniques such as feature extraction and machine learning approaches typically used in pattern classification. While specific pattern classification methods may be introduced later, the foundational knowledge from earlier chapters is crucial for understanding how images are analyzed and classified.

**Answer:**
The textbook does not explicitly cover image pattern classification but provides an introduction to digital image processing fundamentals. These include elements of 